# Exercise 1: MongoDB Query Exercises

This notebook demonstrates several MongoDB operations for the `restaurants` collection. The exercises include:

1. Inserting a new restaurant document (a mock record).
2. Counting the total number of restaurants.
3. Listing all restaurants in the borough **Bronx**.
4. Finding all restaurants serving **Bakery** cuisine with an **A** grade.
5. Updating the grade of the restaurant named **Morris Park Bake Shop** to **A+**.
6. Deleting all restaurants with a grade **C** and then showing the change.

Let's begin!

In [1]:
from pymongo import MongoClient

# Connect to MongoDB (update the URI as needed, e.g., if using Docker it might be mongodb://medical_mongo:27017/)
client = MongoClient("mongodb://localhost:27017/")
db = client["medical_db"]
restaurants_collection = db["restaurants"]

print("Connected to MongoDB. Database: medical_db")

Connected to MongoDB. Database: medical_db


## 1. Insert a New Restaurant Document (Mock Data)

Below, we insert a new restaurant document into the `restaurants` collection. This is a mock document created for testing purposes.

In [2]:
# Define a mock restaurant document
new_restaurant = {
    "restaurant_id": "99999999",
    "name": "Mock Restaurant",
    "borough": "Manhattan",
    "cuisine": "Italian",
    "address": {
        "building": "123",
        "street": "Mockingbird Ln",
        "zipcode": "10001",
        "coord": [-73.985, 40.748] 
    },
    "grades": [
        { "date": "2023-01-01T00:00:00Z", "grade": "B", "score": 10 }
    ]
}

# Insert the document and print the inserted id
result = restaurants_collection.insert_one(new_restaurant)
print(f"Inserted new restaurant with id: {result.inserted_id}")

Inserted new restaurant with id: 683dc836cb2e602c6ceac9e6


## 2. Count the Total Number of Restaurants

Let's count and print the total number of documents in the `restaurants` collection.

In [3]:
# Count total restaurants
total_restaurants = restaurants_collection.count_documents({})
print(f"Total number of restaurants: {total_restaurants}")

Total number of restaurants: 701593


## 3. List All Restaurants in the Borough "Bronx"

The cell below queries for all restaurants located in the borough **Bronx** and prints their names and addresses.

In [4]:
# Query for restaurants in the Bronx
bronx_restaurants = restaurants_collection.find({ "borough": "Bronx" })
print("Restaurants in the Bronx:")
for restaurant in bronx_restaurants:
    print(restaurant["name"], "-", restaurant.get("address", {}))

Restaurants in the Bronx:
Morris Park Bake Shop - {'building': '1007', 'coord': [-73.856077, 40.848447], 'street': 'Morris Park Ave', 'zipcode': '10462'}
Wild Asia - {'building': '2300', 'coord': [-73.8786113, 40.8502883], 'street': 'Southern Boulevard', 'zipcode': '10460'}
Carvel Ice Cream - {'building': '1006', 'coord': [-73.84856870000002, 40.8903781], 'street': 'East 233 Street', 'zipcode': '10466'}
Happy Garden - {'building': '1236', 'coord': [-73.8893654, 40.81376179999999], 'street': '238 Spofford Ave', 'zipcode': '10474'}
Happy Garden - {'building': '277', 'coord': [-73.8941893, 40.8634684], 'street': 'East Kingsbridge Road', 'zipcode': '10458'}
Manhem Club - {'building': '658', 'coord': [-73.81363999999999, 40.82941100000001], 'street': 'Clarence Ave', 'zipcode': '10465'}
The New Starling Athletic Club Of The Bronx - {'building': '2222', 'coord': [-73.84971759999999, 40.8304811], 'street': 'Haviland Avenue', 'zipcode': '10462'}
Yankee Tavern - {'building': '72', 'coord': [-73.

## 4. Find All Restaurants Serving "Bakery" Cuisine with an "A" Grade

Here we search for restaurants with cuisine equal to **Bakery** and that have at least one grade with the value **A**. The query uses the `$elemMatch` operator on the `grades` array.

In [5]:
# Query for restaurants with "Bakery" cuisine and at least one grade of "A"
bakery_a_restaurants = restaurants_collection.find({
    "cuisine": "Bakery",
    "grades": { "$elemMatch": { "grade": "A" } }
})

print("Bakery restaurants with an A grade:")
for restaurant in bakery_a_restaurants:
    print(restaurant["name"], "- Grade(s):", [grade["grade"] for grade in restaurant.get("grades", [])])

Bakery restaurants with an A grade:
Morris Park Bake Shop - Grade(s): ['A', 'A', 'A', 'A', 'B']
Olive'S - Grade(s): ['A', 'A', 'A', 'A', 'A']
Tropical House Baking Co. - Grade(s): ['A', 'A', 'A', 'A']
Cousin John'S Cafe And Bakery - Grade(s): ['A', 'A', 'A', 'A']
Victory Sweet Shop - Grade(s): ['A', 'A', 'A', 'A', 'A', 'A']
De Robertis Pastry Shop - Grade(s): ['A', 'A', 'A', 'A', 'C']
Lefkos Pygos Cafe - Grade(s): ['A', 'A', 'A', 'A', 'A']
Miracali Bakery - Grade(s): ['A', 'A', 'A', 'A']
Little Pie Company - Grade(s): ['A', 'A', 'A', 'A', 'A']
Sybil'S Bakery - Grade(s): ['A', 'A', 'B', 'A', 'A']
Richer'S Bakery - Grade(s): ['A', 'C', 'A', 'A', 'A', 'C']
H & H Midtown Bagels East - Grade(s): ['A', 'A', 'A', 'A', 'B', 'B']
Fay Da Bakery - Grade(s): ['A', 'A', 'A', 'A', 'A']
E & L Bakery & Coffee Shop - Grade(s): ['A', 'A', 'A', 'A']
Sugar Bun Bakery - Grade(s): ['A', 'A', 'B', 'A', 'A']
Caffe Roma - Grade(s): ['A', 'A', 'A', 'A']
La Antioquena Bakery Ii - Grade(s): ['A', 'A', 'B', 'A', '

## 5. Update the Grade of "Morris Park Bake Shop" to "A+"

We update one grade of the restaurant with the name **Morris Park Bake Shop**. In this example, we update the first occurrence where grade is **A** to **A+**. After the update, we print the updated document.

In [6]:
# Update the grade of "Morris Park Bake Shop"
update_result = restaurants_collection.update_one(
    { "name": "Morris Park Bake Shop", "grades.grade": "A" },
    { "$set": { "grades.$.grade": "A+" } }
)

if update_result.modified_count > 0:
    print("Updated grade for Morris Park Bake Shop.")
    # Fetch and print the updated document
    updated_doc = restaurants_collection.find_one({ "name": "Morris Park Bake Shop" })
    print(updated_doc)
else:
    print("No update performed (restaurant not found or grade not matching).")

Updated grade for Morris Park Bake Shop.
{'_id': ObjectId('683dbd0ff1dda2c1451ead89'), 'address': {'building': '1007', 'coord': [-73.856077, 40.848447], 'street': 'Morris Park Ave', 'zipcode': '10462'}, 'borough': 'Bronx', 'cuisine': 'Bakery', 'grades': [{'date': {'$date': 1393804800000}, 'grade': 'A+', 'score': 2}, {'date': {'$date': 1378857600000}, 'grade': 'A', 'score': 6}, {'date': {'$date': 1358985600000}, 'grade': 'A', 'score': 10}, {'date': {'$date': 1322006400000}, 'grade': 'A', 'score': 9}, {'date': {'$date': 1299715200000}, 'grade': 'B', 'score': 14}], 'name': 'Morris Park Bake Shop', 'restaurant_id': '30075445'}


## 6. Delete All Restaurants with Grade "C"

We delete all documents where any grade has the value **C**. Finally, we show the new total count of restaurants in the collection after the deletion.

In [7]:
# Delete all restaurants that have a grade "C"
delete_result = restaurants_collection.delete_many({ "grades.grade": "C" })
print(f"Deleted {delete_result.deleted_count} restaurants with grade C.")

# Show the new total count
new_total = restaurants_collection.count_documents({})
print(f"New total number of restaurants: {new_total}")

Deleted 93744 restaurants with grade C.
New total number of restaurants: 622937
